<a href="https://colab.research.google.com/github/componavt/wd_book/blob/master/programming_tasks/natural_disasters/vuleq_connect/vuleq_connect.ipynb" target="_parent"><img src="https://colab.research.google.com/assets/colab-badge.svg" alt="Open In Colab"/></a>


# This program draws earthquakes, volcanoes and the nearest connections between them at a certain distance on a map of the Earth according to the CSV files earthquakes_2023.csv and volcanoes_2023.csv

Эта программа отрисовывает на карте Земли землетрясения, вулканы и соединяет ближайшие пары на определенном расстоянии по данным из CSV-файлов earthquakes_2023.csv и volcanoes_2023.csv


For the program to work, you need two CSV files generated using SPARQL queries: https://w.wiki/AXz7 and https://w.wiki/AY2R

Для работы программы необходимо два CSV-файла, сгенерированные при помощи SPARQL-запросов: https://w.wiki/AXz7 и https://w.wiki/AY2R

In [19]:
import folium
import csv
import numpy as np
from geopy.distance import geodesic
from scipy.spatial import KDTree
# import pprint # Pretty Print for objects

# Input parameters
dist_max = 100  # maximum distance (km) between volcano and earthquake to draw a line
f_volcano    = "volcanoes_2023.csv"
f_earthquake = "earthquakes_2023.csv"

# Download CSV files from GitHub
!wget https://raw.githubusercontent.com/componavt/wd_book/master/programming_tasks/natural_disasters/vuleq_connect/$f_volcano
!wget https://raw.githubusercontent.com/componavt/wd_book/master/programming_tasks/natural_disasters/vuleq_connect/$f_earthquake

--2025-04-15 14:19:41--  https://raw.githubusercontent.com/componavt/wd_book/master/programming_tasks/natural_disasters/vuleq_connect/volcanoes_2023.csv
Resolving raw.githubusercontent.com (raw.githubusercontent.com)... 185.199.108.133, 185.199.111.133, 185.199.110.133, ...
Connecting to raw.githubusercontent.com (raw.githubusercontent.com)|185.199.108.133|:443... connected.
HTTP request sent, awaiting response... 200 OK
Length: 76165 (74K) [text/plain]
Saving to: ‘volcanoes_2023.csv.3’

volcanoes_2023.csv. 100%[===================>]  74.38K  --.-KB/s    in 0.09s   

2025-04-15 14:19:42 (787 KB/s) - ‘volcanoes_2023.csv.3’ saved [76165/76165]

--2025-04-15 14:19:42--  https://raw.githubusercontent.com/componavt/wd_book/master/programming_tasks/natural_disasters/vuleq_connect/earthquakes_2023.csv
Resolving raw.githubusercontent.com (raw.githubusercontent.com)... 185.199.108.133, 185.199.109.133, 185.199.110.133, ...
Connecting to raw.githubusercontent.com (raw.githubusercontent.com)|185.

In [20]:
!head -n 3 $f_volcano

volcanoLabel;location
Puy Pariou;Point(2.971484 45.796824)
Вануа-Лава;Point(167.466666666 -13.8)


In [21]:
!head -n 3 $f_earthquake

earthquakeLabel;location
1975 Lice earthquake;Point(40.723 38.474)
2011 Hindukush earthquake;Point(71.102 36.502)


In [26]:
# Initialize map
m = folium.Map(zoom_start=2)

# Helper function to parse 'Point(lon lat)' into (lat, lon) tuple
def parse_coords(coord_string):
    lon, lat = map(float, coord_string.replace("Point(", "").replace(")", "").split())
    return (lat, lon)

# Data containers
volcano_coords = []
earthquake_coords = []
volcano_labels = {}
earthquake_labels = {}

# Sets to eliminate duplicate points
seen_volcano_coords = set()
seen_earthquake_coords = set()

# Process volcanoes (CSV)
with open(f_volcano, encoding='utf-8', newline='') as csvfile:
    reader = csv.DictReader(csvfile, delimiter=";")
    for row in reader:
        # Puy Pariou;Point(2.971484 45.796824) -> popup;point(Buff_list1)
		    # Editing the original coordinates

        # pprint.pprint(row) # Prints the nicely formatted dictionary
        popup = row['volcanoLabel']
        coord = parse_coords(row['location'])
        if coord in seen_volcano_coords:
            continue
        seen_volcano_coords.add(coord)
        volcano_coords.append(coord)
        volcano_labels[coord] = popup


# Process earthquakes
with open(f_earthquake, encoding='utf-8', newline='') as csvfile:
    reader = csv.DictReader(csvfile, delimiter=";")
    for row in reader:
        popup = row['earthquakeLabel']
        coord = parse_coords(row['location'])
        if coord in seen_earthquake_coords:
            continue
        seen_earthquake_coords.add(coord)
        earthquake_coords.append(coord)
        earthquake_labels[coord] = popup


# Build KD-tree from volcano coordinates
tree = KDTree(volcano_coords)

# Find the closest volcano to each earthquake
closest_indices = tree.query(earthquake_coords, k=1, distance_upper_bound=dist_max)[1]

# Collect and visualize valid volcano–earthquake pairs
closest_pairs = []
for i, idx in enumerate(closest_indices):
    if idx != len(volcano_coords):  # if valid match found
        eq_coord = earthquake_coords[i]
        volcano_coord = volcano_coords[idx]
        distance = geodesic(eq_coord, volcano_coord).kilometers
        if distance <= dist_max:
            eq_label = earthquake_labels.get(eq_coord, "Unknown EQ")
            vul_label = volcano_labels.get(volcano_coord, "Unknown Volcano")
            closest_pairs.append((eq_coord, eq_label, volcano_coord, vul_label, distance))
            # draw line with label
            folium.PolyLine([eq_coord, volcano_coord], color="purple", weight=1, opacity=1,
                            tooltip=f"{eq_label} ↔ {vul_label} ({distance:.1f} km)").add_to(m)

            # closest_pairs.append((eq_coord, volcano_coord, distance))
            # folium.PolyLine([eq_coord, volcano_coord], color="purple", weight=1, opacity=1).add_to(m)

# Extract coordinates of linked volcanoes and earthquakes
linked_volcano_coords = set(pair[2] for pair in closest_pairs)
linked_earthquake_coords = set(pair[0] for pair in closest_pairs)

# Draw volcanoes with radius depending on whether they are linked
# If the nearest earthquake is found for the volcano, then the circle is larger (radius = 800), otherwise smaller (radius = 500).
for coord in volcano_coords:
    popup = volcano_labels[coord]
    radius = 1300 if coord in linked_volcano_coords else 500
    folium.Circle(radius=radius, location=coord, popup=popup,
                  tooltip=f'Volcano: {popup}', color="red").add_to(m)

# Draw earthquakes
for coord in earthquake_coords:
    popup = earthquake_labels[coord]
    radius = 1300 if coord in linked_earthquake_coords else 500
    folium.Circle(radius=radius, location=coord, popup=popup,
                  tooltip=f'Earthquake: {popup}', color="black").add_to(m)

# Output result
print(f"Number of volcano–earthquake pairs found within {dist_max} km: {len(closest_pairs)}")
print("Example pairs (earthquake ↔ volcano, distance in km):")
for pair in closest_pairs[:5]:
    eq_coord, eq_label, volcano_coord, vul_label, distance = pair
    print(f"{eq_label} ↔ {vul_label}: {distance:.1f} km")
    # print(pair)

# Display the map
m

Number of volcano–earthquake pairs found within 100 km: 455
Example pairs (earthquake ↔ volcano, distance in km):
Q3984663 ↔ Q30144976: 97.5 km
2008 Skåne County earthquake ↔ Central Skåne Volcanic Province: 48.5 km
2011 November Van earthquake ↔ Гиреколь-тепе: 76.3 km
1349 Apennine earthquakes ↔ Camaldoli: 66.5 km
1903 Malazgirt earthquake ↔ Гиреколь-тепе: 66.4 km
